# Cars: Getting Started

In [1]:
import numpy as np 
import pandas as pd 
import seaborn as sns 
import pyblp
sns.set_theme()
import matplotlib.pyplot as plt

pyblp.options.digits = 2
pyblp.options.verbose = False

# Read in data

The dataset, `cars.csv`, contains cleaned and processed data. If you want to make changes, the notebook, `materialize.ipynb`, creates the data from the raw source datsets. 

In [3]:
cars = pd.read_csv('cars.csv') # this reads the *balanced* dataset (i.e. J = 40 products per market always)
# cars = pd.read_excel('cars.xlsx') # this reads the *unbalanced* dataset (i.e. J varies over time)

### No data for France pre 1990. Average growth in adult fraction from other countries applied each year before

In [4]:
AdultFrac = pd.read_excel("FracOver20.xlsx", index_col = 0)
cars['adults'] = None
for idx in cars.index:
    cars['adults'][idx] = AdultFrac[cars['ma'][idx]][cars['ye'][idx]]
cars

/var/folders/qr/xw8cgrnd4098yvfl09hlrdl80000gn/T/ipykernel_32700/1567250594.py:4: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  cars['adults'][idx] = AdultFrac[cars['ma'][idx]][cars['ye'][idx]]
/var/folders/qr/xw8cgrnd4098yvfl09hlrdl80000gn/

ye  ma   co  zcode  brd                     type     brand    model  \
0     70   1   15     14    2             audi 100/200      audi  100/200   
1     70   1   26     35    4  citroen 2 CV 6 - 2 CV 4   citroen     2CV6   
2     70   1   36     36    4            citroen dyane   citroen    dyane   
3     70   1   64     67    7                 fiat 128      fiat      128   
4     70   1   71     80    8              ford escort      ford   escort   
...   ..  ..  ...    ...  ...                      ...       ...      ...   
5995  99   5  914    161   16               mercedes A  mercedes        A   
5996  99   5  936     80    8               ford focus      ford    focus   
5997  99   5  951    208   20              peugeot 206   peugeot      206   
5998  99   5  953    282   29           toyota avensis    toyota  avensis   
5999  99   5  978    287   29             toyota yaris    toyota    yaris   

      org  loc  ...    tax       pop           ngdp          rgdp  \
0       2    4  ...  0.250   9660000  1280999948288  3.940725e+12   
1       1    3  ...  0.250   9660000  1280999948288  3.940725e+12   
2       1    3  ...  0.250   9660000  1280999948288  3.940725e+12   
3       3    5  ...  0.250   9660000  1280999948288  3.940725e+12   
4       2    4  ...  0.250   9660000  1280999948288  3.940725e+12   
...   ...  ...  ...    ...       ...            ...           ...   
5995    2    4  ...  0.175  58200000   889870024704           NaN   
5996    7    4  ...  0.175  58200000   889870024704           NaN   
5997    1    3  ...  0.175  58200000   889870024704           NaN   
5998    4   12  ...  0.175  58200000   889870024704           NaN   
5999    4    6  ...  0.175  58200000   889870024704           NaN   

              engdp         ergdp        engdpc      ergdpc         inc  \
0       25795239936  7.935358e+10   2670.314697  8214.65625  20363.7252   
1       25795239936  7.935358e+10   2670.314697  8214.65625  20363.7252   
2       25795239936  7.935358e+10   2670.314697  8214.65625  20363.7252   
3       25795239936  7.935358e+10   2670.314697  8214.65625  20363.7252   
4       25795239936  7.935358e+10   2670.314697  8214.65625  20363.7252   
...             ...           ...           ...         ...         ...   
5995  1052244508672           NaN  18079.802734         NaN  32434.8905   
5996  1052244508672           NaN  18079.802734         NaN  32434.8905   
5997  1052244508672           NaN  18079.802734         NaN  32434.8905   
5998  1052244508672           NaN  18079.802734         NaN  32434.8905   
5999  1052244508672           NaN  18079.802734         NaN  32434.8905   

        adults  
0     0.688912  
1     0.688912  
2     0.688912  
3     0.688912  
4     0.688912  
...        ...  
5995  0.745551  
5996  0.745551  
5997  0.745551  
5998  0.745551  
5999  0.745551  

[6000 rows x 49 columns]

We estimate that 77% of the adult population have a driving license for a full-car. Hence, the share of population aged 20+ with a driver becomes:

In [7]:
license_share = 0.77
cars["ad_w_li"] = cars["adults"] * license_share 

In [14]:
lbl_vars = pd.read_csv('labels_variables.csv', index_col=0)
lbl_vals = pd.read_stata('cars.dta', iterator=True).value_labels() # the values that variables take (not relevant for all )

## Overview of the dataset

In [15]:
pd.set_option('display.max_colwidth', None)
tab = cars.mean(numeric_only=True).apply(lambda x: f'{x:.2f}').to_frame('Mean').join(lbl_vars)
tab

Mean  \
ye                   84.50   
ma                    3.00   
co                  207.50   
zcode               177.76   
brd                  16.79   
org                   2.72   
loc                   5.17   
cla                   2.30   
home                  0.32   
frm                  14.50   
qu                35606.68   
cy                 1337.09   
hp                   50.10   
we                  934.49   
pl                    4.88   
do                    3.55   
le                  409.24   
wi                  163.44   
he                  140.46   
li1                   6.59   
li2                   8.11   
li3                   8.92   
li                    7.87   
sp                  154.22   
ac                   16.27   
pr              2608988.58   
princ                 0.76   
eurpr              7256.92   
exppr            600384.65   
avexr               229.30   
avdexr              319.91   
avcpr               492.53   
avppr               671.77   
avdcpr               77.02   
avdppr               87.69   
xexr                 66.32   
tax                   0.21   
pop            49183800.00   
ngdp    178667304825541.97   
rgdp    216716720230172.44   
engdp      504371708122.45   
ergdp      659002565347.56   
engdpc            10015.84   
ergdpc            13264.84   
inc               26829.74   
qu_tot          1424267.29   
logp                  8.69   

                                                                                   label  
ye                                                      year (=first dimension of panel)  
ma                                                   market (=second dimension of panel)  
co                                                model code (=third dimension of panel)  
zcode               alternative model code (predecessors and successors get same number)  
brd                                                                           brand code  
org              origin code (demand side, country with which consumers associate model)  
loc                location code (production side, country where producer produce model)  
cla                                                                class or segment code  
home                          domestic car dummy (appropriate interaction of org and ma)  
frm                                                                            firm code  
qu                                               sales (number of new car registrations)  
cy                                               cylinder volume or displacement (in cc)  
hp                                                                    horsepower (in kW)  
we                                                                        weight (in kg)  
pl                                                places (number, not reliable variable)  
do                                                 doors (number, not reliable variable)  
le                                                                        length (in cm)  
wi                                                                         width (in cm)  
he                                                                        height (in cm)  
li1                             measure 1 for fuel efficiency (liter per km, at 90 km/h)  
li2                            measure 2 for fuel efficiency (liter per km, at 120 km/h)  
li3                          measure 3 for fuel efficiency (liter per km, at city speed)  
li                                             average of li1, li2, li3 (used in papers)  
sp                                                               maximum speed (km/hour)  
ac          time to acceleration (in seconds from 0 to 100 km/h, some from 0 to 96 km/h)  
pr                                      price (in destination currency including V.A.T.)  
princ   =pr/(ngdp/pop): price relative to per capita income (often used in demand model)  
eurpr   =pr/avdexr: price in comm

# Set up for analysis

## Price variables 

Can be either price (`pr`), price-to-income (`princ`), or log price (`logp`, created below).

In [16]:
price_var = 'eurpr'

In [17]:
cars['logp'] = np.log(cars[price_var])

## Market share

**Todo:** Decide how to measure the market size and thereby the market share. *Note:* Below is just an example that sets the market size = population / 3. 

In [18]:
# total quantity of cars sold in market-year (ma, ye)
cars['qu_tot'] = cars.groupby(['ma', 'ye'])['qu'].transform('sum')
cars['market_size'] = cars['pop'] * cars['ad_w_li']
cars['s'] = cars['qu'] / cars['market_size']

In [19]:
# compute the share of the outside good (will be useful for the demand inversion)
cars['s0'] = 1.0 - cars.groupby(['ma', 'ye'])['s'].transform('sum')
print(f'Outside share is from {cars.s0.min():.1%} to {cars.s0.max():.1%}')

Outside share is from 92.7% to 97.1%


In [20]:
cars.groupby(['ma'])['s'].describe().rename(index=lbl_vals['market']).style.format('{:.3f}')

## 1. Using canned software

In [21]:
from linearmodels.iv import IV2SLS

In [22]:
cars['delta'] = cars['s'] / cars['s0']
cars['delta'] = np.log(cars['delta'].values.astype(float)) ## Den stoppede med at ville gøre det i et skridt uden at definere type

In [23]:
cars["brand"].replace('alfa romeo', 'alfa_romeo', inplace=True)
cars["brand"] = cars["brand"].str.replace('/', '', regex=False)

/var/folders/qr/xw8cgrnd4098yvfl09hlrdl80000gn/T/ipykernel_32700/3195240017.py:1: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  cars["brand"].replace('alfa romeo', 'alfa_romeo', inplace=True)


In [24]:
categorical_var = 'brand' # name of categorical variable
dummies = pd.get_dummies(cars[categorical_var]) # creates a matrix of dummies for each value of dummyvar
x_vars_dummies = list(dummies.columns[1:].values) # omit a reference category, here it is the first (hence columns[1:])

# add dummies to the dataframe 
assert dummies.columns[0] not in cars.columns, f'It looks like you have already added this dummy to the dataframe. Avoid duplicates! '
cars = pd.concat([cars,dummies], axis=1)

In [32]:
cars['avg_eurpr_ye_ma'] = cars.groupby(['ye', 'ma'])['eurpr'].transform('mean')
cars['log_avg_eurpr_ye_ma'] = np.log(cars['avg_eurpr_ye_ma'])

In [33]:
# choose your preferred variables 
x_vars = ['logp', 'log_avg_eurpr_ye_ma', 'home', 'cy', 'hp', 'we', 'li', 'sp'] + x_vars_dummies # <--- !!! CHOOSE HERE 
print(x_vars)

['logp', 'log_avg_eurpr_ye_ma', 'home', 'cy', 'hp', 'we', 'li', 'sp', 'MCC', 'VW', 'alfa_romeo', 'audi', 'citroen', 'daewoo', 'daf', 'fiat', 'ford', 'honda', 'hyundai', 'innocenti', 'lancia', 'mazda', 'mercedes', 'mitsubishi', 'nissan', 'opel', 'peugeot', 'renault', 'rover', 'saab', 'seat', 'skoda', 'suzuki', 'talbot', 'talhillman', 'talmatra', 'talsimca', 'talsunb', 'toyota', 'volvo']


In [34]:
formula = 'delta ~ 1'
for x_ in x_vars:
    formula += ' + ' + x_
print(formula)
model = IV2SLS.from_formula(formula, cars).fit()

delta ~ 1 + logp + log_avg_eurpr_ye_ma + home + cy + hp + we + li + sp + MCC + VW + alfa_romeo + audi + citroen + daewoo + daf + fiat + ford + honda + hyundai + innocenti + lancia + mazda + mercedes + mitsubishi + nissan + opel + peugeot + renault + rover + saab + seat + skoda + suzuki + talbot + talhillman + talmatra + talsimca + talsunb + toyota + volvo


/opt/anaconda3/lib/python3.12/site-packages/linearmodels/iv/model.py:557: MissingValueWarning: 
Inputs contain missing values. Dropping rows with missing observations.
  super().__init__(


In [35]:
model.summary

<class 'linearmodels.compat.statsmodels.Summary'>
"""
                            OLS Estimation Summary                            
==============================================================================
Dep. Variable:                  delta   R-squared:                      0.4054
Estimator:                        OLS   Adj. R-squared:                 0.4015
No. Observations:                5998   F-statistic:                 1.503e+05
Date:                Fri, Oct 18 2024   P-value (F-stat)                0.0000
Time:                        10:54:53   Distribution:                 chi2(40)
Cov. Estimator:                robust                                         
                                                                              
                                  Parameter Estimates                                  
=======================================================================================
                     Parameter  Std. Err.     T-stat    P-value    Lower CI    Upper CI
---------------------------------------------------------------------------------------
Intercept              -9.2192     0.2582    -35.706     0.0000     -9.7253     -8.7131
logp                   -0.5258     0.0902    -5.8308     0.0000     -0.7026     -0.3491
log_avg_eurpr_ye_ma     0.5530     0.0823     6.7220     0.0000      0.3918      0.7143
home                    1.0384     0.0233     44.575     0.0000      0.9928      1.0841
cy                     -0.0001  7.755e-05    -1.8706     0.0614     -0.0003   6.932e-06
hp                     -0.0290     0.0022    -13.114     0.0000     -0.0333     -0.0247
we                      0.0008     0.0001     5.2725     0.0000      0.0005      0.0011
li                     -0.0128     0.0114    -1.1214     0.2621     -0.0351      0.0095
sp                      0.0185     0.0017     10.729     0.0000      0.0151      0.0219
MCC                    -1.2242     0.1401    -8.7370     0.0000     -1.4989     -0.9496
VW                      0.0192     0.0585     0.3277     0.7431     -0.0955      0.1338
alfa_romeo             -0.5773     0.0660    -8.7462     0.0000     -0.7067     -0.4479
audi                   -0.1425     0.0585    -2.4374     0.0148     -0.2570     -0.0279
citroen                -0.4600     0.0551    -8.3568     0.0000     -0.5679     -0.3522
daewoo                 -0.7853     0.1625    -4.8339     0.0000     -1.1038     -0.4669
daf                    -0.8127     0.1614    -5.0357     0.0000     -1.1290     -0.4964
fiat                   -0.3249     0.0552    -5.8876     0.0000     -0.4330     -0.2167
ford                    0.0567     0.0534     1.0628     0.2879     -0.0479      0.1614
honda                  -0.3378     0.0760    -4.4431     0.0000     -0.4869     -0.1888
hyundai                -1.0105     0.1279    -7.9024     0.0000     -1.2611     -0.7598
innocenti              -1.3255     0.2278    -5.8184     0.0000     -1.7720     -0.8790
lancia                 -0.8707     0.0755    -11.527     0.0000     -1.0188     -0.7227
mazda                  -0.2831     0.0668    -4.2401     0.0000     -0.4139     -0.1522
mercedes                0.4276     0.0602     7.1078     0.0000      0.3097      0.5454
mitsubishi             -0.3302     0.0738    -4.4738     0.0000     -0.4748     -0.1855
nissan                 -0.2891     0.0550    -5.2547     0.0000     -0.3969     -0.1812
opel                   -0.0747     0.0571    -1.3082     0.1908     -0.1867      0.0372
peugeot                -0.2128     0.0568    -3.7478     0.0002     -0.3241     -0.1015
renault                -0.1042     0.0517    -2.0148     0.0439     -0.2056     -0.0028
rover                  -0.5528     0.0610    -9.0643     0.0000     -0.6724     -0.4333
saab                   -0.9507     0.1556    -6.1090     0.0000     -1.2557     -0.6457
seat                   -0.8274     0.0715    -11.572     0.0000     -0.9676     -0.6873
skoda                  -1.1237     0.1131    -9.9394     0.0000    

In [19]:
K = len(x_vars)
N = cars.ma.nunique() * cars.ye.nunique()
J = 40 
x = cars[x_vars].values.reshape((N,J,K)).astype(float)
cars['outcome'] = cars['s'] / cars['s0']
y = cars['delta'].values.reshape((N,J))
# standardize x
x = ((x - x.mean(0).mean(0))/(x.std(0).std(0)))

# Towards non-linear estimation

In order to work with the logit model, you have to be able to compute the utility indices, which typically take the form of some inner product of an $x$-vector and a $\theta$ vector. This is illustrated for you below. Since `x` is `(N,J,K)` (i.e. `x[i,j,:]` gives the $K$-vector of regressors for the car `j` in market-period `i`), we just have to form the matrix product `x @ theta`, and Python will do the sum over the 3rd dimension of `x`. 

In [ ]:
theta0 = np.zeros((K,))
v = x @ theta0 # how to multiply a trial value with the matrix of regressors 
np.exp(v) / np.sum(np.exp(v), 1, keepdims=True) # choice probabilities 